<h2 align="center">Silver Layer</h2>
The data from the bronze layer is brought into the silver layer.

**Input data:** Staging tables: stg_orders, stg_products, stg_customers

**Transformations:** 
1. Customer Name and Phone Number in stg_customer table are cleansed and enriched. 
2. New column 'rounded_price' is added to stg_orders and stg_products tables to act as a composite key for join operations.
3. Data type of Price column in stg_orders is changed to double datatype.

**Output data:** Refined and enriched tables: ref_orders, ref_products, ref_customers.


In [0]:
%run /Users/vishnuas1987@gmail.com/PEI_Case_Study/Functions/PEI_transformation_functions

In [0]:
from pyspark.sql.functions import col,lit,to_date,round
from pyspark.sql import DataFrame
from pyspark.sql.functions import transform
from pyspark.sql.types import DateType
from pyspark.sql.functions import split

In [0]:
try:

    #create orders,products and customers dataframe from staging table
    df_products = spark.table("stg_products")
    df_customers = spark.table("stg_customers")
    df_orders = spark.table("stg_orders")

    #transform the customer data by cleaning Customer Name and Phone number.
    df_customers_trans = df_customers.transform(remove_non_alphabet,'Customer_Name').transform(enrich_name,'Customer_Name','email').transform(clean_phone_number,'phone')

    #transform the product data by creating a new column called rounded_price to be used for composite key with product_id
    df_product_trans = df_products.withColumn("rounded_price", round(col("Price_per_product")))

    #transform the orders data by 
    #       1. changing the data type of Price column to double
    #       2. creating a new column rounded_price to prevent duplication of product data while joining with products table
    #       3. making sure the null columns in rounded_price is set to 0.       
    df_orders_trans = df_orders.withColumn("Price", col("Price").cast("double")).\
        withColumn("Order_year", split(df_orders["Order_Date"], "/")[2]).\
            withColumn("rounded_price", round(col("Price") / col("Quantity"))).\
                withColumn("rounded_price", when(col("rounded_price").isNull(), 0).otherwise(col("rounded_price")))

    #write the orders, products and customer data into refined/silver layer
    df_customers_trans.write.format("delta").saveAsTable("ref_customers")
    df_product_trans.write.format("delta").saveAsTable("ref_products")
    df_orders_trans.write.format("delta").saveAsTable("ref_orders")  

except Exception as e:
    print("Error occurred while creating silver layer", str(e))

In [0]:
%sql
select * from ref_orders;

Customer_ID Discount Order_Date Order_ID Price Product_ID Profit Quantity Row_ID Ship_Date Ship_Mode Order_year rounded_price JK-15370 0.3 21/8/2016 CA-2016-122581 573.174 FUR-CH-10002961 63.686 7 1 25/8/2016 Standard Class 2016 82.0 BD-11320 0.0 23/9/2017 CA-2017-117485 291.96 TEC-AC-10004659 102.186 4 2 29/9/2017 Standard Class 2017 73.0 LB-16795 0.7 6/10/2016 US-2016-157490 17.0 OFF-BI-10002824 -14.92 4 3 7/10/2016 First Class 2016 4.0 KB-16315 0.2 2/7/2015 CA-2015-111703 15.552 OFF-PA-10003349 5.6376 3 4 9/7/2015 Standard Class 2015 5.0 DO-13435 0.2 3/10/2014 CA-2014-108903 142.488 TEC-AC-10003023 -3.0 3 5 3/10/2014 Same Day 2014 47.0 CB-12025 0.0 27/11/2016 CA-2016-117583 79.95 OFF-BI-10004233 38.376 5 6 30/11/2016 First Class 2016 16.0 SM-20005 0.0 10/12/2014 CA-2014-148488 11.0 OFF-PA-10004470 5.2256 2 7 15/12/2014 Standard Class 2014 6.0 RD-19480 0.0 1/12/2016 CA-2016-136434 17.31 FUR-FU-10001196 5.193 3 8 7/12/2016 Standard Class 2016 6.0 JM-16195 0.0 30/4/2014 CA-2014-160094 826.0 OFF-ST-10000585 214.0 5 9 2/5/2014 First Class 2014 165.0 SC-20230 0.0 3/8/2017 CA-2017-141747 16.06 OFF-ST-10003996 4.1756 1 10 8/8/2017 Second Class 2017 16.0 BO-11350 0.2 3/5/2017 CA-2017-132199 8.0 OFF-FA-10002280 2.8 2 11 8/5/2017 Standard Class 2017 4.0 BD-11320 0.2 27/11/2017 CA-2017-107125 117.488 OFF-BI-10001989 41.1208 7 12 2/12/2017 Standard Class 2017 17.0 AB-10105 0.7 19/9/2017 CA-2017-153822 18.18 OFF-BI-10001460 -13.938 4 13 25/9/2017 Standard Class 2017 5.0 NP-18670 0.0 12/10/2017 CA-2017-150091 45.0 TEC-AC-10002167 4.0 3 14 16/10/2017 Standard Class 2017 15.0 KD-16270 0.0 2/9/2016 CA-2016-130407 39.98 FUR-FU-10001967 9.995 2 15 6/9/2016 Standard Class 2016 20.0 BF-11005 0.6 28/7/2016 US-2016-105452 302.0 FUR-FU-10003806 -378.4 5 16 1/8/2016 Standard Class 2016 60.0 LE-16810 0.8 27/5/2014 US-2014-117058 17.46 OFF-BI-10004139 -30.555 6 17 30/5/2014 First Class 2014 3.0 TT-21070 0.0 13/11/2017 CA-2017-122490 344.91 OFF-ST-10000991 10.3473 3 18 18/11/2017 Standard Class 2017 115.0 CA-12055 0.2 22/11/2016 US-2016-164945 134.272 OFF-BI-10001524 46.9952 8 19 27/11/2016 Standard Class 2016 17.0 GD-14590 0.0 5/5/2014 CA-2014-111934 11.88 OFF-BI-10004364 5.0 2 20 7/5/2014 First Class 2014 6.0 DK-12895 0.0 8/3/2015 CA-2015-105627 373.08 FUR-FU-10000308 82.0776 6 21 12/3/2015 Standard Class 2015 62.0 RM-19675 0.0 19/11/2014 CA-2014-158274 503.96 TEC-PH-10003273 131.0296 4 22 24/11/2014 Second Class 2014 126.0 MY-18295 0.0 28/4/2014 CA-2014-118976 5.34 OFF-AR-10004752 1.4952 2 23 3/5/2014 Standard Class 2014 3.0 DB-13555 0.2 14/9/2017 CA-2017-115882 74.352 OFF-PA-10001125 23.235 3 24 17/9/2017 First Class 2017 25.0 JS-15880 0.0 21/12/2015 US-2015-126214 1618.0 FUR-TA-10003748 356.0414 13 25 24/12/2015 Second Class 2015 124.0 MJ-17740 0.0 11/3/2017 CA-2017-147291 895.92 OFF-BI-10003091 421.0824 4 26 17/3/2017 Standard Class 2017 224.0 JL-15835 0.0 17/12/2015 US-2015-138121 142.36 FUR-CH-10004875 38.4372 2 27 17/12/2015 Same Day 2015 71.0 PF-19120 0.8 7/4/2015 CA-2015-140025 463.248 OFF-AP-10002651 -1181.2824 8 28 11/4/2015 Standard Class 2015 58.0 KB-16315 0.0 26/8/2014 CA-2014-103331 3.38 OFF-PA-10002659 1.5548 1 29 1/9/2014 Standard Class 2014 3.0 DO-13645 0.0 4/12/2017 CA-2017-118003 302.94 FUR-CH-10004860 18.1764 3 30 10/12/2017 Standard Class 2017 101.0 PG-18820 0.0 27/7/2015 US-2015-129553 29.97 TEC-PH-10004897 0.2997 3 31 2/8/2015 Standard Class 2015 10.0 AJ-10780 0.0 14/5/2017 US-2017-133361 14.0 OFF-AR-10003045 6.615 5 32 17/5/2017 First Class 2017 3.0 JG-15115 0.7 3/12/2015 CA-2015-123092 95.0 OFF-BI-10001718 -73.577 5 33 7/12/2015 Standard Class 2015 19.0 SC-20380 0.2 3/2/2017 CA-2017-126354 115.296 OFF-PA-10004381 40.3536 3 34 8/2/2017 Standard Class 2017 38.0 KH-16630 0.0 18/9/2015 CA-2015-109575 499.99 TEC-PH-10000730 129.9974 1 35 23/9/2015 Standard Class 2015 500.0 KL-16555 0.7 26/12/2014 CA-2014-111451 78.6 OFF-BI-10004593 -62.88 5 36 28/12/2014 First Class 2014 16.0 TH-21550 0.0 26/6/2017 CA-2017-133256 543.92 TEC-PH-10

In [0]:
%sql
select * from ref_products;

Product_ID Category Sub_Category Product_Name State Price_per_product rounded_price FUR-CH-10002961 Furniture Chairs Leather Task Chair, Black New York 81.882 82.0 TEC-AC-10004659 Technology Accessories Imation Secure+ Hardware Encrypted USB 2.0 Flash Drive; 16GB Oklahoma 72.99 73.0 OFF-BI-10002824 Office Supplies Binders Recycled Easel Ring Binders Colorado 4.25 4.0 OFF-PA-10003349 Office Supplies Paper Xerox 1957 Florida 5.184 5.0 TEC-AC-10003023 Technology Accessories Logitech G105 Gaming Keyboard Ohio 47.496 47.0 OFF-BI-10004233 Office Supplies Binders GBC Pre-Punched Binding Paper, Plastic, White, 8-1/2" x 11" New Jersey 15.99 16.0 OFF-PA-10004470 Office Supplies Paper Adams Write n' Stick Phone Message Book, 11" X 5 1/4", 200 Messages New York 5.5 6.0 FUR-FU-10001196 Furniture Furnishings DAX Cubicle Frames - 8x10 Indiana 5.77 6.0 OFF-ST-10000585 Office Supplies Storage Economy Rollaway Files Kentucky 165.2 165.0 OFF-ST-10003996 Office Supplies Storage Letter/Legal File Tote with Clear Snap-On Lid, Black Granite Washington 16.06 16.0 OFF-FA-10002280 Office Supplies Fasteners Advantus Plastic Paper Clips Pennsylvania 4.0 4.0 OFF-BI-10001989 Office Supplies Binders Premium Transparent Presentation Covers by GBC California 16.784 17.0 OFF-BI-10001460 Office Supplies Binders Plastic Binding Combs Arizona 4.545 5.0 TEC-AC-10002167 Technology Accessories Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive New Jersey 15.0 15.0 FUR-FU-10001967 Furniture Furnishings Telescoping Adjustable Floor Lamp New York 19.99 20.0 FUR-FU-10003806 Furniture Furnishings Tenex Chairmat w/ Average Lip, 45" x 53" Texas 60.4 60.0 OFF-BI-10004139 Office Supplies Binders Fellowes Presentation Covers for Comb Binding Machines Illinois 2.91 3.0 OFF-ST-10000991 Office Supplies Storage Space Solutions HD Industrial Steel Shelving. Washington 114.97 115.0 OFF-BI-10001524 Office Supplies Binders GBC Premium Transparent Covers with Diagonal Lined Pattern New York 16.784 17.0 OFF-BI-10004364 Office Supplies Binders Storex Dura Pro Binders Virginia 5.94 6.0 FUR-FU-10000308 Furniture Furnishings Deflect-o Glass Clear Studded Chair Mats Wisconsin 62.18 62.0 TEC-PH-10003273 Technology Phones AT&T TR1909W Louisiana 125.99 126.0 OFF-AR-10004752 Office Supplies Art Blackstonian Pencils Maryland 2.67 3.0 OFF-PA-10001125 Office Supplies Paper Xerox 1988 North Carolina 24.784 25.0 FUR-TA-10003748 Furniture Tables Bevis 36 x 72 Conference Tables Washington 124.4615385 124.0 OFF-BI-10003091 Office Supplies Binders GBC DocuBind TL200 Manual Binding Machine Michigan 223.98 224.0 FUR-CH-10004875 Furniture Chairs Harbour Creations 67200 Series Stacking Chairs Michigan 71.18 71.0 OFF-AP-10002651 Office Supplies Appliances Hoover Upright Vacuum With Dirt Cup Texas 57.906 58.0 OFF-PA-10002659 Office Supplies Paper Avoid Verbal Orders Carbonless Minifold Book Delaware 3.38 3.0 FUR-CH-10004860 Furniture Chairs Global Low Back Tilter Chair New Jersey 100.98 101.0 TEC-PH-10004897 Technology Phones Mediabridge Sport Armband iPhone 5s Kentucky 9.99 10.0 OFF-AR-10003045 Office Supplies Art Prang Colored Pencils Maryland 2.8 3.0 OFF-BI-10001718 Office Supplies Binders GBC DocuBind P50 Personal Binding Machine North Carolina 19.0 19.0 OFF-PA-10004381 Office Supplies Paper 14-7/8 x 11 Blue Bar Computer Printout Paper Florida 38.432 38.0 TEC-PH-10000730 Technology Phones Samsung Galaxy S4 Active Maryland 499.99 500.0 OFF-BI-10004593 Office Supplies Binders Ibico Laser Imprintable Binding System Covers Colorado 15.72 16.0 TEC-PH-10002660 Technology Phones Nortel Networks T7316 E Nt8 B27 Michigan 67.99 68.0 OFF-EN-10003001 Office Supplies Envelopes Ames Color-File Green Diamond Border X-ray Mailers Texas 67.184 67.0 FUR-BO-10003034 Furniture Bookcases O'Sullivan Elevations Bookcase, Cherry Finish New York 104.784 105.0 OFF-PA-10001878 Office Supplies Paper Xerox 1891 Texas 39.128 39.0 OFF-BI-10003707 Office Supplies Binders Aluminum Screw Posts Texas 3.052 3.0 OFF-BI-10001249 Office Supplie

In [0]:
%sql
select * from ref_customers;

Customer_ID Customer_Name email phone address Segment Country City State Postal_Code Region name_filled _cleaned_phone LW-16990 Lindsay Williams angelahoward623@gmail.com 853-660-7372x805 58474 Lopez Port
New Chadtown, IL 55760 Corporate United States Monroe North Carolina 28110 South false +1(853)660-7372x805 YS-21880 Yana Sorensen tylerjones637@gmail.com 912-445-7716x34658 5856 Nicole Crest Apt. 004
North Christineland, PW 84482 Corporate United States Los Angeles California 90036 West false +1(912)445-7716x34658 EH-14125 Eugene Hildebrand karenjacobs432@gmail.com #ERROR! 589 Stacey Prairie Suite 695
East Justin, DC 94097 Home Office United States Philadelphia Pennsylvania 19140 East false Invalid phone number BT-11305 Beth Thompson audreyrichardson371@gmail.com -3305 589 Wilson Club
North Lisaside, DE 98079 Home Office United States Superior Wisconsin 54880 Central false Invalid phone number EB-13750 Edward Becker thomashickman353@gmail.com (300)852-8375x7146 58996 Anthony Trafficway Suite 095
Port Melissa, MT 84143 Corporate United States Plantation Florida 33317 South false +1(300)852-8375x7146 KH-16630 Ken Heidel randyelliott568@gmail.com 709-181-6245x66499 59023 Boyd Forest Apt. 266
Port Davidmouth, CT 34959 Corporate United States Clinton Maryland 20735 East false +1(709)181-6245x66499 EM-14095 Eudokia Martin markstewart528@gmail.com 5087731130 594 Cheyenne Heights Apt. 511
Rileyland, IL 73967 Corporate United States Springfield Virginia 22153 South false +1(508)773-1130 MH-17290 Marc Harrigan anthonysmith783@gmail.com #ERROR! 5949 Nancy Road
Lake Todd, MD 59856 Home Office United States Los Angeles California 90036 West false Invalid phone number AR-10510 Andrew Roberts janiceroman109@gmail.com (185)406-7142x057 5953 Gill Centers
Masontown, MI 39024 Consumer United States Philadelphia Pennsylvania 19134 East false +1(185)406-7142x057 TC-21295 Toby Carlisle dianaherring411@gmail.com #ERROR! 5955 Jennifer Lakes Apt. 153
South Kevin, MP 42733 Consumer United States San Diego California 92024 West false Invalid phone number FC-14335 Fred Chung matthewhogan675@gmail.com 224.046.5899x6684 5955 Jessica Cove
East Ginaburgh, MN 19795 Corporate United States Pueblo Colorado 81001 West false +1(224)046-5899x6684 JR-16210 Justin Ritter jonathanclark863@gmail.com 293-097-5033x062 59694 Kenneth Orchard
South Brendaport, CA 29492 Corporate United States Columbus Indiana 47201 Central false +1(293)097-5033x062 DP-13105 Dave Poirier michaellopez745@gmail.com 534-497-4017 598 Ashley Run
Brownmouth, NH 20431 Corporate United States Philadelphia Pennsylvania 19134 East false +1(534)497-4017 KS-16300 Karen Seio jefferypeterson263@gmail.com 001-450-530-0545 603 Sophia Harbors Apt. 633
Edwardfurt, CO 20814 Corporate United States Columbus Georgia 31907 South false +1(450)530-0545 DW-13540 Don Weiss markrivers649@gmail.com 696-932-2805 60437 Williams Stream Apt. 817
Emilymouth, GA 94269 Consumer United States Seattle Washington 98105 West false +1(696)932-2805 PJ-19015 Pauline Johnson julierogers229@gmail.com 617-913-2741x3442 6063 Bender Mountains Suite 816
Phillipside, NM 15455 Consumer United States New York City New York 10024 East false +1(617)913-2741x3442 JS-15940 Joni Sundaresam melissawilson600@gmail.com (879)655-4559 60749 Javier View Apt. 637
North Chad, HI 53479 Home Office United States Lancaster Ohio 43130 East false +1(879)655-4559 SG-20080 Sandra Glassco philipvargas623@gmail.com 001-699-396-4378 608 Joseph Groves
New Damon, MN 88274 Consumer United States Redlands California 92374 West false +1(699)396-4378 AG-10390 Allen Goldenen codylyons721@gmail.com 271-660-8219 60971 Carrillo Square Suite 141
New Kimberlybury, AS 02128 Consumer United States Cincinnati Ohio 45231 East false +1(271)660-8219 NG-18355 Nat Gilpin amandaromero232@gmail.com 639-800-7127x57046 610 Proctor Ferry Apt. 716
Ellenberg, PR 37379 Corporate United States Newark Ohio 43055 East false +1(639)800-7127x57046 TP-21415 Tom Prescott elizabethsmith907@gmail.c